
# Quantile Regression Workflows

<span style="font-size: 18pt; font-style: italic; font-weight: bold">Data Science Study Group South FL</span>   

<span style="font-size: 16pt; ont-weight: bold">Anton Antonov</span>

<span style="font-size: 14pt; font-style: italic;">January 2025</span>

----

## Abstract

### Short

This talk showcases and exemplifies the rapid specification and execution of Quantile Regression workflows. Various use cases are discussed, including fitting, outlier detection, conditional CDFs, and simulations, using different types of time series data.

### Longer


Quantile Regression (QR) is a powerful analysis method that is often considered superior to other regression techniques. The benefits of QR are highlighted in this talk through multiple examples from various "real-life" time series, such as finance, weather, and human activities. The use of QR for fitting, outlier detection, conditional CDFs, and simulations will be demonstrated. The analysis is significantly simplified with the new Python package ["Regressionizer"](https://pypi.org/project/Regressionizer/), [AAp1], which allows for quick setup and execution of QR workflows.

This presentation is intended for data analysts, data scientists, engineers, and anyone with an interest in time series analysis. A basic understanding of Python is all that is required from the audience, as the coding pipelines have been designed to be straightforward and easy to follow.

### Teaser

![](https://raw.githubusercontent.com/antononcube/MathematicaVsR/refs/heads/master/Projects/QuantileRegressionWorkflows/Presentation-documents-useR-ODSC-Boston-2019-04-18/0-XKCD-2048-vs-QRMon.png)


------

## Workflows flowchart

The following flowchart summarizes the workflows that are supported by [`Regressionizer`](https://pypi.org/project/Regressionizer/):

![](https://raw.githubusercontent.com/antononcube/Python-Regressionizer/main/docs/img/Quantile-regression-workflow-extended.jpg)

In [1]:
# First example
# (Regressionizer(data)
#     .quantile_regression(8, probs=[0.1, 0.5, 0.9])
#     .plot(title = "Quantile Regression (first example)", template=template, width = 600, height = 500)
#     .take_value()
#     .show())

-------

## Setup

Load the "Regressionizer" and other "standard" packages:

In [2]:
from Regressionizer import *
from OutlierIdentifiers import *

import numpy as np
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
import plotly.subplots as sp

import random

In [3]:
template='plotly_dark'
data_color='darkgray'

### Temperature data

In [4]:
url = "https://raw.githubusercontent.com/antononcube/MathematicaVsR/master/Data/MathematicaVsR-Data-Atlanta-GA-USA-Temperature.csv"
dfTemperature = pd.read_csv(url)
dfTemperature['DateObject'] = pd.to_datetime(dfTemperature['Date'], format='%Y-%m-%d')
dfTemperature = dfTemperature[(dfTemperature['DateObject'].dt.year >= 2020) & (dfTemperature['DateObject'].dt.year <= 2023)]
dfTemperature

Date  AbsoluteTime  Temperature DateObject
2555  2020-01-01    3786825600         7.56 2020-01-01
2556  2020-01-02    3786912000         7.28 2020-01-02
2557  2020-01-03    3786998400        12.28 2020-01-03
2558  2020-01-04    3787084800        12.78 2020-01-04
2559  2020-01-05    3787171200         4.83 2020-01-05
...          ...           ...          ...        ...
4011  2023-12-27    3912624000        11.67 2023-12-27
4012  2023-12-28    3912710400         7.44 2023-12-28
4013  2023-12-29    3912796800         3.78 2023-12-29
4014  2023-12-30    3912883200         4.83 2023-12-30
4015  2023-12-31    3912969600         1.17 2023-12-31

[1461 rows x 4 columns]

### Financial data

In [5]:
dirName = "../../../Python-Regressionizer/Regressionizer/resources"
fileName = dirName + "/dfFinancialData.csv.zip"
dfFinancialData = pd.read_csv(fileName, compression='zip')
dfFinancialData['Time'] = pd.to_datetime(dfFinancialData['Time'], format='%Y-%m-%d')
dfFinancialData['Time'] = dfFinancialData['Time'].apply(lambda x: x.timestamp())

dfFinancialData

Time       Value
0     1.388621e+09  109.526901
1     1.388707e+09  109.447281
2     1.388966e+09  108.571083
3     1.389053e+09  108.690544
4     1.389139e+09  108.371948
...            ...         ...
1253  1.545610e+09   32.361740
1254  1.545782e+09   34.559715
1255  1.545869e+09   33.998539
1256  1.545955e+09   35.120903
1257  1.546214e+09   35.401508

[1258 rows x 2 columns]


### Distribution data

Generate random data:

In [6]:
np.random.seed(0)
x = np.linspace(0, 2, 300)
y = np.sin(2 * np.pi * x) + np.random.normal(0, 0.4, x.shape)
data = np.column_stack((x, y))

In [7]:
xs = np.arange(-3, 3.01, 0.01)
dfDistributionData = pd.DataFrame({
    'X': xs,
    'Y': [np.exp(-x**2) + np.random.normal(0, 0.15 * np.sqrt(abs(1.5 - x) / 1.5)) for x in xs]
})
dfDistributionData

X         Y
0   -3.00 -0.339322
1   -2.99  0.430447
2   -2.98 -0.030493
3   -2.97 -0.175978
4   -2.96  0.172517
..    ...       ...
596  2.96 -0.126601
597  2.97 -0.228766
598  2.98  0.386700
599  2.99 -0.060271
600  3.00 -0.219136

[601 rows x 2 columns]

In [8]:
data = dfDistributionData.to_numpy()

Plot the generated data:

In [9]:
fig = px.scatter(x=data[:, 0], y=data[:, 1], labels={'x': 'X-axis', 'y': 'Y-axis'}, template=template, width = 800, height = 600)
fig.show()

-------

## Fit B-splines

Here is a "quick" fit using a B-spline basis:

In [53]:
obj = Regressionizer(data).quantile_regression(knots=10, probs=[0.2, 0.5, 0.8]).plot(title="B-splines fit", template=template)

Show the obtained plot:

In [54]:
obj.take_value().show()

Here is a dictionary of the found regression quantiles:

In [55]:
obj.take_regression_quantiles()

{0.2: <function QuantileRegression.QuantileRegression._make_combined_function.<locals>.<lambda>(x)>,
 0.5: <function QuantileRegression.QuantileRegression._make_combined_function.<locals>.<lambda>(x)>,
 0.8: <function QuantileRegression.QuantileRegression._make_combined_function.<locals>.<lambda>(x)>}

------

## Best / unique features 

Why prefer using Quantile Regression (QR)?

- Robust wrt Outliers

- Conditional Cumulative Distribution Function (CDF)

    - For both analysis and simulations ⭐️

- Variance estimates (by default)

- Relaxed assumptions of signal variance

    - [Heteroscedastic](https://en.wikipedia.org/wiki/Homoscedasticity_and_heteroscedasticity) signals are fine with QR

- Easy finding of contextual outliers and anomalies ⭐️

------

## Fit given functions

Define a list of functions:

In [10]:
funcs = [lambda x: 1, lambda x: x, lambda x: np.cos(x), lambda x: np.cos(3 * x), lambda x: np.cos(6 * x)]

In [11]:
def chebyshev_t_polynomials(n):
    if n == 0:
        return lambda x: 1
    elif n == 1:
        return lambda x: x
    else:
        T0 = lambda x: 1
        T1 = lambda x: x
        for i in range(2, n + 1):
            Tn = lambda x, T0=T0, T1=T1: 2 * x * T1(x) - T0(x)
            T0, T1 = T1, Tn
        return Tn

chebyshev_polynomials = [chebyshev_t_polynomials(i) for i in range(8)]

Define ***regression quantile*** probabilities:

In [12]:
probs = [0.1, 0.5, 0.9]

Perform Quantile Regression and (non-linear) Least Squares Fit:

In [13]:
obj2 = (
    Regressionizer(data)
    .echo_data_summary()
    .quantile_regression_fit(funcs=chebyshev_polynomials, probs=probs)
    .least_squares_fit(funcs=chebyshev_polynomials)
    .plot(title = "Quantile Regression and Least Squares fitting using Chebyshev polynomials", template=template)
)

Statistic    Regressor | Value
------------ --------------------
min                -3.0 | -0.6634155270368904
25%          -1.500000000000032 | 0.004469472579252067
median       -6.394884621840902e-14 | 0.1568399089941699
75%          1.499999999999904 | 0.5766190556497813
max          2.999999999999872 | 1.1916829958389759


Plot the obtained regression quantilies and least squares fit:

In [14]:
obj2.take_value().show()

The ***regression quantiles** separate the data according to the given probabilities:

In [15]:
obj2.separate(cumulative=True, fractions=True).take_value()

{0.1: 0.1048252911813644, 0.5: 0.5008319467554077, 0.9: 0.9018302828618968}

-------

## Robust regression with "strong" outliers

Quantile Regression is robust when outliers in the data are present.

(Similar to how in 1D data the median is a more robust estimator than the mean.)

Here a few points of the distribution data above are "significantly pulled up":

In [19]:
data.shape

(601, 2)

In [20]:
data2 = data.copy()
data2[580,1] = 40
data2[590,1] = 40

Let us do the fit again:

In [21]:
obj3 = (
    Regressionizer(data2)
    .echo_data_summary()
    .quantile_regression_fit(funcs=chebyshev_polynomials, probs=probs)
    .least_squares_fit(funcs=chebyshev_polynomials)
    .plot(title = "Quantile Regression and Least Squares fitting using Chebyshev polynomials", template=template)
)

Statistic    Regressor | Value
------------ --------------------
min                -3.0 | -0.6634155270368904
25%          -1.500000000000032 | 0.006027320587706912
median       -6.394884621840902e-14 | 0.15899224900969233
75%          1.499999999999904 | 0.5867731753300555
max          2.999999999999872 |       40.0


Here is the plot (the mean is very biased!):

In [22]:
fig = obj3.take_value()
fig.update_layout(yaxis=dict(range=[-0.7,1.4]))

fig.show()

------

## Weather temperature data

Convert to "numpy" array: 

In [23]:
temp_data = dfTemperature[['AbsoluteTime', 'Temperature']].to_numpy()
temp_data.shape

(1461, 2)

Here is pipeline for Quantile Regression computation and making of a corresponding plot:

In [24]:
obj = (
    Regressionizer(temp_data)
    .echo_data_summary()
    .quantile_regression(knots=16, probs=[0.02, 0.5, 0.98])
    .date_list_plot(title="Atlanta, Georgia, USA, Temperature, ℃", template=template, data_color=data_color, width = 1200)
)

Statistic    Regressor | Value
------------ --------------------
min          3786825600.0 |     -11.89
25%          3818361600.0 |      10.06
median       3849897600.0 |      16.94
75%          3881433600.0 |      22.56
max          3912969600.0 |      32.39


Show the obtained plot:

In [25]:
obj.take_value().show()

Here we show the fractions of the number of points under each regression quantile:

In [26]:
obj.separate(cumulative=True, fractions=True).take_value()

{0.02: 0.025325119780971937, 0.5: 0.5017111567419575, 0.98: 0.9801505817932923}

**Remark:** If the quantile regression algorithms work correctly then the cumulation separation fractions correspond -- i.e. are nearly equal - to the probabilities of the regression quantiles.

-------

## Fitting errors

### Errors

Here the absolute fitting errors are computed and the average is for each is computed:

In [27]:
{ k : np.mean(np.array(d)[:,1]) for k, d in obj.errors(relative_errors=False).take_value().items() }

{0.02: 7.8147302053170264, 0.5: 0.11949615503066727, 0.98: -7.317147013894586}

### Error plots

Here we give the fitting errors (residuals) for the regression quantiles found and plotted above:

In [28]:
obj.error_plots(relative_errors=False, date_plot=True, template=template, width=1200, height=300).take_value().show()

------

## Outliers

One way to find _contextual_ outliers in time series is to find regression quantiles at low- and high enough probabilities, and then select the points "outside" of those curves:

In [29]:
obj = (
    Regressionizer(temp_data)
    .quantile_regression(knots=20, probs=[0.01,  0.99], order=3)
    .outliers()
)

obj.take_value()

{'bottom': [array([ 3.7885536e+09, -3.1100000e+00]),
  array([3.7919232e+09, 3.2800000e+00]),
  array([3.795552e+09, 7.390000e+00]),
  array([3.7977984e+09, 9.2800000e+00]),
  array([3.7982304e+09, 1.0220000e+01]),
  array([3.8068704e+09, 2.0110000e+01]),
  array([3.8097216e+09, 1.2390000e+01]),
  array([ 3.8225088e+09, -4.7200000e+00]),
  array([3.8298528e+09, 1.0220000e+01]),
  array([3.8333952e+09, 1.8720000e+01]),
  array([3.8458368e+09, 3.5000000e+00]),
  array([ 3.8524896e+09, -2.3900000e+00])],
 'top': [array([3.7944288e+09, 2.2390000e+01]),
  array([3.802896e+09, 2.756000e+01]),
  array([3.8040192e+09, 2.7940000e+01]),
  array([3.8129184e+09, 2.3000000e+01]),
  array([3.814128e+09, 2.128000e+01]),
  array([3.820608e+09, 1.778000e+01]),
  array([3.8258784e+09, 2.3500000e+01]),
  array([3.8326176e+09, 2.7060000e+01]),
  array([3.839184e+09, 2.617000e+01]),
  array([3.8420352e+09, 2.2780000e+01]),
  array([3.8641536e+09, 2.9830000e+01]),
  array([3.8727072e+09, 2.5610000e+01]),
  

Here we plot the outliers (using a "narrower band" than above):

In [30]:
obj = (
    Regressionizer(temp_data)
    .quantile_regression(knots=20, probs=[0.02,  0.98], order=3)
    .outliers_plot(
        title="Outliers of Atlanta, Georgia, USA, Temperature, ℃",
        date_plot=True, 
        template=template,
        data_color=data_color,
        width = 1200, height = 400)
)

obj.take_value().show()

------

## Point anomalies

Here is pipeline for Quantile Regression computation and making of a corresponding plot:

In [31]:
obj = (
    Regressionizer(dfFinancialData.to_numpy())
    .echo_data_summary()
    .quantile_regression(knots=12, probs=[0.5], order = 2)
    .date_list_plot(title="Financial data", template=template, data_color=data_color, width = 1200)
)

Statistic    Regressor | Value
------------ --------------------
min          1388620800.0 | 31.3365592956543
25%          1428019200.0 | 99.1304168701172
median       1467288000.0 | 108.033164978027
75%          1506621600.0 | 127.5753574371335
max          1546214400.0 | 142.674545288086


Show the obtained plot:

In [32]:
fig = obj.take_value()
fig.show()

In [33]:
outliers = (obj
.find_anomalies_by_residuals(
    relative_errors=True,
    threshold=None, 
    outlier_identifier=quartile_identifier_parameters)
.take_value());

fig.add_trace(go.Scatter(x=to_datetime_index(outliers[:,0]), y=outliers[:,1], mode='markers', name='Outliers', marker_color = "orange"))

In [34]:
outliers = (obj
.find_anomalies_by_residuals(
    relative_errors=False,
    threshold=None, 
    outlier_identifier=hampel_identifier_parameters)
.take_value());

fig.add_trace(go.Scatter(x=to_datetime_index(outliers[:,0]), y=outliers[:,1], mode='markers', name="Outliers 2", marker_color = "Red"))

---------

## Pick points along regression quantiles  

Here is a workflow that finds a regression quantile for probability `0.5` and pick data points around it:

In [35]:
probs = [0.3,]
obj=(
    Regressionizer(temp_data)
    .quantile_regression(knots=20, probs=probs)
    .pick_path_points(threshold=1.5, relative_errors=False)
    )

path_points = np.array(obj.take_value()[probs[0]])
dfPathPoints = pd.DataFrame(path_points)
dfPathPoints

0     1
0    3.786826e+09  7.56
1    3.786912e+09  7.28
2    3.787258e+09  6.67
3    3.787430e+09  6.72
4    3.787517e+09  7.11
..            ...   ...
455  3.911501e+09  2.94
456  3.911587e+09  2.00
457  3.911674e+09  2.50
458  3.911933e+09  3.00
459  3.912970e+09  1.17

[460 rows x 2 columns]

Get the a `Figure` object from the `Regressionizer` object:

In [36]:
fig = obj.date_plot(width=1200, template=template, data_color=data_color).take_value()

Plot the data and the path points:

In [37]:
fig.add_trace(go.Scatter(x=to_datetime_index(path_points[:,0]), y=path_points[:,1], mode='markers', name='Picked points'))
fig.show()

Plot just the path points:

In [38]:
fig = px.scatter(x=dfPathPoints.iloc[:,0], y=dfPathPoints.iloc[:,1], template=template, width=1200)

fig.show()

--------

## Conditional CDF

Here is a list of probabilities to be used to reconstruct Cumulative Distribution Functions (CDFs):

In [39]:
probs = np.sort(np.concatenate((np.arange(0.1, 1.0, 0.1), [0.01, 0.99])))
probs

array([0.01, 0.1 , 0.2 , 0.3 , 0.4 , 0.5 , 0.6 , 0.7 , 0.8 , 0.9 , 0.99])

Here we find the regression quantiles for those probabilities:

In [40]:
obj=(
    Regressionizer(temp_data)
    .quantile_regression(knots=20,probs=probs)
    .date_list_plot(template=template, data_color="darkgray", width=1200)
    )

Here we show the plot obtained above:

In [41]:
obj.take_value().show()

### Get CDF function

Here we take a date in ISO format and convert to number of seconds since 1900-01-01:

In [42]:
from datetime import datetime

iso_date = "2022-01-01"
date_object = datetime.fromisoformat(iso_date)
epoch = datetime(1900, 1, 1)

focusPoint = int((date_object - epoch).total_seconds())
print(focusPoint)

3849984000


Here the _conditional_ CDF at that date is computed:

In [43]:
aCDFs = obj.conditional_cdf(focusPoint).take_value()
aCDFs

{3849984000: <scipy.interpolate._interpolate.interp1d at 0x12ef76710>}

Plot the obtained CDF function:

In [44]:
xs = np.linspace(obj.take_regression_quantiles()[0.01](focusPoint), obj.take_regression_quantiles()[0.99](focusPoint), 20)
cdf_values = [aCDFs[focusPoint](x) for x in xs]

fig = go.Figure(data=[go.Scatter(x=xs, y=cdf_values, mode='lines')])
# Update layout
fig.update_layout(
    title='Temperature Data CDF at ' + str(focusPoint),
    xaxis_title='Temperature',
    yaxis_title='Probability',
    template=template,
    legend=dict(title='Legend'),
    height=300,
    width=800
)
fig.show()

### Plot multiple CDFs

Here are few dates converted into number of seconds since 1990-01-01:

In [45]:
pointsForCDFs = [focusPoint + i * 365 * 24 * 3600 for i in range(-1,2)]
pointsForCDFs

[3818448000, 3849984000, 3881520000]

Here are the plots of CDF at those dates:

In [46]:
obj.conditional_cdf_plot(pointsForCDFs, title = 'CDFs', template=template).take_value().show()

-----

## Simulation

Here is a pipeline that produces simulated time series based on fitted regression quantiles:

In [47]:
sim_points = (
    Regressionizer(temp_data)
    .echo_data_summary()
    .quantile_regression(knots=20, probs=[0.001, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9, 0.999])
    .simulate(800)
    .take_value()
)

Statistic    Regressor | Value
------------ --------------------
min          3786825600.0 |     -11.89
25%          3818361600.0 |      10.06
median       3849897600.0 |      16.94
75%          3881433600.0 |      22.56
max          3912969600.0 |      32.39


Here is the plot of the original and simulated time series:

In [48]:
fig = sp.make_subplots(rows=2, cols=1, subplot_titles=['Original time series', 'Simulated time series'])
fig.add_trace(go.Scatter(x=to_datetime_index(temp_data[:,0]), y=temp_data[:,1], mode='lines', name=None), row = 1, col = 1)
fig.add_trace(go.Scatter(x=to_datetime_index(sim_points[:,0]), y=sim_points[:,1], mode='lines', name=None), row = 2, col = 1)
fig.update_layout(template=template, title = "Weather temperature data", showlegend=False)
fig.show()

-----

## Big picture

- Having a "complete" set of Machine Learning (ML) workflows in several programming languages.
  - The focus is on Python, R, and Wolfram Language (WL).
- Python's Quantile Regression pipeline implementation was missing for years.
- Code generation using both:
  - Large Language Models (LLM)
  - Grammar-based interpreters (ie. "Small Language Models")

----- 

## LLM support 

Code generation via LLMs can be done using:

1. Examples of natural language phrases/commands to pipeline segments
2. Question Answering System (QAS)

Here is an example of QSA via LLMs:

In [50]:
%%bash
concretize -l=Python Make a quantile regression pipeline, using 20 nodes and the data set dfTemperature


qrObj = (Regressionizer(None)
.echo_data_summary()
.quantile_regression(knots = 12, probs = [{0.25, 0.5, 0.75}], order = 3)
.plot(date_plot = False)
.error_plots(relative_errors = False, date_plot = False))


In [51]:
dfTemperature

Date  AbsoluteTime  Temperature DateObject
2555  2020-01-01    3786825600         7.56 2020-01-01
2556  2020-01-02    3786912000         7.28 2020-01-02
2557  2020-01-03    3786998400        12.28 2020-01-03
2558  2020-01-04    3787084800        12.78 2020-01-04
2559  2020-01-05    3787171200         4.83 2020-01-05
...          ...           ...          ...        ...
4011  2023-12-27    3912624000        11.67 2023-12-27
4012  2023-12-28    3912710400         7.44 2023-12-28
4013  2023-12-29    3912796800         3.78 2023-12-29
4014  2023-12-30    3912883200         4.83 2023-12-30
4015  2023-12-31    3912969600         1.17 2023-12-31

[1461 rows x 4 columns]

In [52]:
qrObj = (Regressionizer(dfTemperature[["AbsoluteTime", "Temperature"]].to_numpy())
.echo_data_summary()
.quantile_regression(knots = 20, probs = [0.25, 0.5, 0.75], order = 3)
.plot(date_plot = True, template = template)
)


Statistic    Regressor | Value
------------ --------------------
min          3786825600.0 |     -11.89
25%          3818361600.0 |      10.06
median       3849897600.0 |      16.94
75%          3881433600.0 |      22.56
max          3912969600.0 |      32.39


In [ ]:
qrObj.take_value().show()

-----

##  History





- Quantile Regression (QR) started mid 18th century
    - For Astronomy-related problems 
        - Similar to Linear Regression (LR)
- Recently (≈ 50 years ago) Roger Koenker et al. introduced modern computational framework for QR
    - And worked out QR-based inference

### Previous work on software packages

Roger Koenker implemented the R package "quantreg", [RKp1].
Anton Antonov implemented the R package "QRMon-R" for the specification of monadic pipelines for doing QR, [AAp1].

Several Wolfram Language (aka Mathematica) packages are implemented by Anton Antonov, see [AAp1, AAp2, AAf1].

**Remark:** The paclets at the Wolfram Language Paclet Repository were initially Mathematica packages hosted at GitHub.
The Wolfram Function Repository function
[`QuantileRegression`](https://resources.wolframcloud.com/FunctionRepository/resources/QuantileRegression/), [AAf1]
does only B-spline fitting.

I have made a series of lectures on Quantile Regression for Wolfram U; see:

- ["**[LiVE] Quantile Regression Workflows (WL Live-Stream Series)**"](https://community.wolfram.com/groups/-/m/t/1787896)

-----

## Questions (anticipated)

- Can we do Multi-dimensional Quantile Regression (QR)?
- How QR compares with ARIMA?
    - QR can be used instead of ARIMA.
- What happens when fitting through only few points?
- What other anomaly detection methods can be used?
- Is there are a list of all "good" features QR?

Detailed answers to QR FAQ can be found here:

- ["Simplified Machine Learning Workflows with Anton Antonov, Session #5: Quantile Regression (Part 5)
"](https://www.youtube.com/watch?v=MUD7lNltHdA)

In [ ]:
# A few points
points = [(random.uniform(0, 10), random.uniform(0, 100)) for _ in range(6)]
points = sorted(points, key=lambda point: point[0])

# Quantile regression
obj = Regressionizer(np.array(points) ).quantile_regression( knots = 2, probs = [0.5, ], order = 2).plot(template = template, width = 600, height = 300)
obj.take_value().show()

------

## References

### Articles, books

[RK1] Roger Koenker, 
[Quantile Regression](https://books.google.com/books/about/Quantile_Regression.html?id=hdkt7V4NXsgC), 
Cambridge University Press, 2005.

[RK2] Roger Koenker,
["Quantile Regression in R: a vignette"](https://cran.r-project.org/web/packages/quantreg/vignettes/rq.pdf),
(2006),
[CRAN](https://cran.r-project.org/).

[AA1] Anton Antonov,
["A monad for Quantile Regression workflows"](https://github.com/antononcube/MathematicaForPrediction/blob/master/MarkdownDocuments/A-monad-for-Quantile-Regression-workflows.md),
(2018),
[MathematicaForPrediction at GitHub](https://github.com/antononcube/MathematicaForPrediction).

### Packages, paclets

[AAp1] Anton Antonov,
[Quantile Regression Python package](https://github.com/antononcube/Python-Regressionizer),
(2024),
[GitHub/antononcube](https://github.com/antononcube).

[AAp2] Anton Antonov,
[`QRMon-R`](https://github.com/antononcube/QRMon-R),
(2019),
[GitHub/antononcube](https://github.com/antononcube).

[AAp3] Anton Antonov,
[Quantile Regression WL paclet](https://github.com/antononcube/WL-QuantileRegression-paclet),
(2014-2023),
[GitHub/antononcube](https://github.com/antononcube).

[AAp4] Anton Antonov,
[Monadic Quantile Regression WL paclet](https://github.com/antononcube/WL-MonadicQuantileRegression-paclet),
(2018-2024),
[GitHub/antononcube](https://github.com/antononcube).

[AAf1] Anton Antonov,
[`QuantileRegression`](https://resources.wolframcloud.com/FunctionRepository/resources/QuantileRegression),
(2019),
[Wolfram Function Repository](https://resources.wolframcloud.com/FunctionRepository/resources/QuantileRegression).

[RKp1] Roger Koenker,
[`quantreg`](https://cran.r-project.org/web/packages/quantreg/index.html),
[CRAN](https://cran.r-project.org/).

### Repositories

[AAr1] Anton Antonov,
[DSL::English::QuantileRegressionWorkflows in Raku](https://github.com/antononcube/Raku-DSL-English-QuantileRegressionWorkflows),
(2020),
[GitHub/antononcube](https://github.com/antononcube/Raku-DSL-English-QuantileRegressionWorkflows).


### Videos

[AAv1] Anton Antonov,
["Boston useR! QuantileRegression Workflows 2019-04-18"](https://www.youtube.com/watch?v=a_Dk25xarvE),
(2019),
[Anton Antonov at YouTube](https://www.youtube.com/@AAA4Prediction).

[AAv2] Anton Antonov,
["useR! 2020: How to simplify Machine Learning workflows specifications"](https://www.youtube.com/watch?v=b9Uu7gRF5KY),
(2020),
[R Consortium at YouTube](https://www.youtube.com/channel/UC_R5smHVXRYGhZYDJsnXTwg).